In [1]:
import xarray as xr
import pandas as pd
import numpy as np

import plotly.graph_objects as go
import plotly.express as px


In [2]:
# Cargar el archivo NetCDF
ds = xr.open_dataset('WRFPrecip_horario.nc')
print(ds)

<xarray.Dataset>
Dimensions:  (Time: 1, south_north: 230, west_east: 251, time: 72)
Coordinates:
    XLAT     (Time, south_north, west_east) float32 ...
    XLONG    (Time, south_north, west_east) float32 ...
    XTIME    (time, Time) datetime64[ns] ...
Dimensions without coordinates: Time, south_north, west_east, time
Data variables:
    PRECIP   (time, Time, south_north, west_east) float32 ...


In [3]:
laststep = ds.isel(time=45)
xtime = pd.to_datetime(laststep['XTIME'].values[0]).strftime('%d-%m-%Y %H:%M')
# Extraer las variables de latitud y longitud
lat = ds['XLAT']
lon = ds['XLONG']
data = laststep['PRECIP']

In [4]:
# Crear un DataFrame para plotly
df = pd.DataFrame({
    'lat': lat.values.flatten(),
    'lon': lon.values.flatten(),
    'data': data.values.flatten()
})
df['data'] = df['data'].replace(0, np.nan)  # Reemplazar 0 con NaN para mostrar blanco

# Crear la figura con plotly express
fig = px.density_mapbox(
    df, lat='lat', lon='lon', z='data', 
    radius=10, 
    center=dict(lat=df['lat'].mean(), lon=df['lon'].mean()), 
    zoom=6,
    mapbox_style='carto-positron',
    color_continuous_scale='viridis',
    #range_color=(0.01, np.nanmax(df['data']))
    range_color=(0.01, 100)
)

# Configurar el diseño del gráfico
fig.update_layout(
    title=f'Fecha de pronóstico: {xtime}',
    coloraxis_colorbar=dict(title='Precip (mm)'),
    mapbox=dict(
        layers=[
            # Agregar los límites de los países
            {
                'source': 'https://raw.githubusercontent.com/nvkelso/natural-earth-vector/master/geojson/ne_50m_admin_0_boundary_lines_land.geojson',
                'below': 'traces',
                'type': 'line',
                'color': 'black',
                'opacity': 0.5
            },
            # Agregar la línea costera
            {
                'source': 'https://raw.githubusercontent.com/nvkelso/natural-earth-vector/master/geojson/ne_50m_coastline.geojson',
                'below': 'traces',
                'type': 'line',
                'color': 'black',
                'opacity': 0.5
            }
        ]
    ),
    width = 1000,
    height = 800
)

# Mostrar el gráfico interactivo
fig.show()